In [10]:
import pandas as pd
import folium

# Define the path to your CSV file
csv_file_path = '../sim_data/fcd_data_e2w_out_2020-01-02_100.csv'

# Read the CSV file into a pandas DataFrame
try:
    df = pd.read_csv(csv_file_path)
    print(f"Successfully read {csv_file_path}. First 5 rows:")
    print(df.head())
except FileNotFoundError:
    print(f"Error: File not found at {csv_file_path}")
    df = None
except Exception as e:
    print(f"An error occurred while reading the CSV file: {e}")
    df = None

Error: File not found at ../sim_data/fcd_data_e2w_out_2020-01-02_100.csv


In [8]:
# Check if DataFrame was loaded successfully and has necessary columns
if df is not None and 'y' in df.columns and 'x' in df.columns:
    # Assuming 'y' is Latitude and 'x' is Longitude
    # Create a base map centered around the mean coordinates
    # Handle potential errors if y or x columns contain non-numeric data after reading
    try:
        mean_lat = df['y'].mean()
        mean_lon = df['x'].mean()
        m = folium.Map(location=[mean_lat, mean_lon], zoom_start=12)

        # Add circle markers for each data point
        # It's good practice to handle potential NaNs in location columns
        for index, row in df.iterrows():
            # Check for NaN values in latitude and longitude
            if pd.notna(row['y']) and pd.notna(row['x']):
                # Create a popup with relevant information from the row
                popup_html = f"""
                <b>ID:</b> {row.get('id', 'N/A')}<br>
                <b>Time:</b> {row.get('time', 'N/A')}<br>
                <b>Speed:</b> {row.get('speed', 'N/A')}<br>
                <b>Lane:</b> {row.get('lane', 'N/A')}
                """
                # Use CircleMarker instead of Marker
                folium.CircleMarker(
                    [row['y'], row['x']],
                    radius=5, # Define the size of the circle marker in pixels
                    color='blue', # Border color
                    fill=True,
                    fill_color='blue', # Fill color
                    fill_opacity=0.6, # Opacity of the fill color
                    popup=popup_html
                ).add_to(m)
            else:
                print(f"Skipping row {index} due to missing coordinates: lat={row['y']}, lon={row['x']}")

        # Display the map (or save to an HTML file)
        # To display in a Jupyter notebook/Lab, the map object itself is usually enough
        # To save to HTML, uncomment the line below:
        # m.save('fcd_data_map.html')
        print("Map created. Displaying map object...")
        m

    except KeyError as e:
        print(f"Error: Missing expected column for mapping: {e}")
    except ValueError as e:
        print(f"Error: Coordinate columns contain non-numeric data: {e}")
    except Exception as e:
        print(f"An unexpected error occurred during map creation: {e}")
elif df is not None:
    missing_cols = [col for col in ['y', 'x'] if col not in df.columns]
    print(f"Error: DataFrame is missing required coordinate columns: {', '.join(missing_cols)}")
else:
    print("Cannot create map because the DataFrame was not loaded successfully.")

Map created. Displaying map object...


In [9]:
m